## Task 3

- Given is a list of textual descriptions for around 20,000 companies (provided in the file Company Descriptions). There are 2 types of descriptions – long and short. Use your discretion while using either.

### Task 3.1

- 3.1: Classify these companies based on their descriptions to only one of the industries from the industry labels given (provided in the file: Industry Segments – Top 10 Keywords). Your output should contain the company name and the corresponding industry segment assigned by your algorithm.     


In [1]:
#Importing libraries
import pandas as pd
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel
import numpy as np
import gensim.downloader as api
import nltk
import re

In [3]:
# Loading data
company_data = pd.read_csv('Company Descriptions.csv')
industry_data = pd.read_csv('Industry Segments - Top 10 Keywords.csv')

In [4]:
# finding null descriptions in company_description
company_data['company_description'].isnull().sum()

728

In [7]:
# finding null descriptions in company_short_description
company_data['company_short_description'].isnull().sum()

0

In [8]:
company_data.head(20)

company_name  \
0                Codementor   
1                   AgShift   
2                    Shipsi   
3                  OpenNews   
4          Biobot Analytics   
5                  NetClerk   
6                 Satellier   
7                  MedCases   
8                 SpeedDate   
9     Raven Biotechnologies   
10             Kids on 45th   
11          Xtreme Spectrum   
12     WindMIL Therapeutics   
13                   Alacra   
14                  PetDesk   
15               BrightDime   
16  Comstellar Technologies   
17                    Lot18   
18                     ROAM   
19                 Homebase   

                            company_short_description  \
0   Codementor is an online marketplace connecting...   
1   AgShift is designing world's most advanced aut...   
2   Shipsi empowers any retailer with the ability ...   
3   OpenNews helps a global network of developers,...   
4   Biobot Analytics analyzes city sewage to estim...   
5   NetClerk is an application service provider (A...   
6   Satellier provides workshare solutions for the...   
7   MedCases, an Internet-based provider of intera...   
8   SpeedDate.com is an online webcam-enhanced dat...   
9   Raven biotechnologies is focused on the develo...   
10  building a box of kid's everyday essentials wi...   
11  Xtreme Spectrum is a provider of ultra-wideban...   
12  WindMIL Therapeutics is developing cell therap...   
13                 Information and workflow solutions   
14  PetDesk offers CRM software for pet care provi...   
15  BrightDime offers everything your company need...   
16  At Comstellar Technologies, Inc., we're buildi...   
17  Lot18 is an online marketer and seller of wine...   
18  ROAM is a global community for the next genera...   
19  Homebase is the easiest way to track hours and...   

                                  company_description  
0   Codementor provides live 1:1 help for software...  
1   AgShift solution blends Deep Learning with Com...  
2   Shipsi empowers any retailer with the ability ...  
3   We're helping a global network of developers, ...  
4   Biobot Analytics analyzes sewage to estimate o...  
5   As of April 22, 2002, NetClerk Inc. was acquir...  
6   Satellier is one of the world's leading author...  
7   MedCases focuses on the development of medical...  
8   SpeedDate.com is one of a slew of new online, ...  
9   Raven biotechnologies, Inc., a biotechnology c...  
10                                                NaN  
11  XtremeSpectrum  is a developer of ultrawideban...  
12  WindMIL Therapeutics is developing cell therap...  
13  Alacra organizes financial and legal informati...  
14  PetDesk is a SaaS appointment and reminder pla...  
15  We're an independent, unbiased ally helping em...  
16  At Comstellar Technologies, Inc., we're buildi...  
17  Lot18 is a membership by invitation website fo...  
18                                                NaN  
19  Homebase helps to reduce the administrative bu...

In [9]:
# Filling null values in company_description with company_short_description.
company_data['company_description'].fillna(company_data['company_short_description'], inplace=True)


In [10]:
company_data['company_description'].isnull().sum()

0

In [11]:
# Preprocessing the data
def preprocess_text(text):
        # Removing special characters and digits
        text = re.sub(r'[^a-zA-Z ]', '', text)
        # Converting to lowercase
        text = text.lower()
        return text

company_data['company_description'] = company_data['company_description'].apply(preprocess_text)
# removing comma between tags
industry_data['Tags'] = industry_data['Tags'].apply(lambda x: x.lower().replace(',', ' '))

In [12]:
company_data['company_description'][1]

'agshift solution blends deep learning with computer vision to autonomously inspect produce and other commodities for defects it does quality assessments and makes judgements as per usda specifications or organizations own specifications the patented deep learning models analyze the defects in the sample images and predict the overall quality of the sample the platform relies on curated extensive realworld image data sets to teach our software to analyze defects with high consistency and accuracy  every time  the solution augments manual inspections  providing objective consistent and standardized quality interpretation across the supply chain  every single time '

In [13]:
industry_data['Tags'].head()

0    security  systems  video  surveillance  servic...
1    service  cleantech  water  agriculture  traits...
2    developer  treatment  drug  diseases  technolo...
3    service  platform  online  management  data  m...
4    service  wireless  network  data  internet  ap...
Name: Tags, dtype: object

In [14]:
# Initializing WordNetLemmatizer and stopwords
lemmatizer = WordNetLemmatizer()
stop_words = set(stopwords.words("english"))

In [15]:
# creating lemmetizing function and removing stopwords
def lemmatize_text(text):
    return ' '.join([lemmatizer.lemmatize(word) for word in text.split() if word not in stop_words])

In [16]:
# applying lemmetizing function and removing stopwords on company_description and Tags
company_data['company_description'] = company_data['company_description'].apply(lemmatize_text)
industry_data['Tags'] = industry_data['Tags'].apply(lemmatize_text)

In [17]:
# splitting tags and storing it in the form of list
industry_data['Tags'] = industry_data['Tags'].str.split()

In [18]:
industry_data['Tags'][0]

['security',
 'system',
 'video',
 'surveillance',
 'service',
 'aircraft',
 'military',
 'system',
 'technology',
 'flight']

In [19]:
# i will be using the Google News word vectors to find synonym words for tags
word_vectors = api.load("word2vec-google-news-300") #loading API


In [20]:
# defining a function to find synonyms and similar words for each tag in the list of Tags
def find_similar_words(tags, word_vectors, threshold=0.6):
    similar_words = []
    for tag in tags:
        if tag in word_vectors.key_to_index:  # Check if the tag exists in the word vectors
            expanded_words = [word for word, _ in word_vectors.most_similar(positive=[tag], topn=10) if _ >= threshold]
            similar_words.extend(expanded_words)
    return list(set(similar_words))


In [21]:
# Find and add synonyms and similar words for each word in the list of Tags
industry_data['Tags'] = industry_data['Tags'].apply(lambda tags: tags + find_similar_words(tags, word_vectors))


In [22]:
industry_data['Tags'][0]

['security',
 'system',
 'video',
 'surveillance',
 'service',
 'aircraft',
 'military',
 'system',
 'technology',
 'flight',
 'surveilance',
 'surveillence',
 'miltary',
 'planes',
 'Armed_Forces',
 'Video',
 'plane',
 'innovations',
 'video_clips',
 'surveillance_cameras',
 'airplanes',
 'jets',
 'aircrafts',
 'vidoe',
 'flight_BA###',
 'Surveillance',
 'armed_forces',
 'technological_advancement',
 'Army',
 'technologies',
 'Aircraft',
 'technological_innovation',
 'twin_engined_aircraft',
 'videotape',
 'Flight',
 'flights',
 'footage',
 'army',
 'systems',
 'airplane',
 'technological_innovations',
 'survelliance',
 'secu_rity',
 'INCLUDES_previously_unreleased',
 'naval',
 'civilian',
 'sytem',
 'cutting_edge',
 'videos',
 'Military',
 'services',
 'secuirty',
 'miliary',
 'Watch_TimesCast_daily',
 'Efforting_soundbites',
 'jet',
 'technol',
 'surviellance',
 'Security',
 'aicraft',
 'militarys',
 'ser_vice']

In [23]:
# since some tags are capitalize therefore we will make all the tags lower again
industry_data['Tags'] = industry_data['Tags'].apply(lambda tags: [tag.lower() for tag in tags])

In [24]:
industry_data['Tags'][0]

['security',
 'system',
 'video',
 'surveillance',
 'service',
 'aircraft',
 'military',
 'system',
 'technology',
 'flight',
 'surveilance',
 'surveillence',
 'miltary',
 'planes',
 'armed_forces',
 'video',
 'plane',
 'innovations',
 'video_clips',
 'surveillance_cameras',
 'airplanes',
 'jets',
 'aircrafts',
 'vidoe',
 'flight_ba###',
 'surveillance',
 'armed_forces',
 'technological_advancement',
 'army',
 'technologies',
 'aircraft',
 'technological_innovation',
 'twin_engined_aircraft',
 'videotape',
 'flight',
 'flights',
 'footage',
 'army',
 'systems',
 'airplane',
 'technological_innovations',
 'survelliance',
 'secu_rity',
 'includes_previously_unreleased',
 'naval',
 'civilian',
 'sytem',
 'cutting_edge',
 'videos',
 'military',
 'services',
 'secuirty',
 'miliary',
 'watch_timescast_daily',
 'efforting_soundbites',
 'jet',
 'technol',
 'surviellance',
 'security',
 'aicraft',
 'militarys',
 'ser_vice']

In [25]:
company_data['company_description'][0]

'codementor provides live help software development making easy developer connect expert via screen sharing video chat two way get help ondemand live expert help longterm dedicated mentorship build project faster ondemand help topic including ruby python php javascript csshtml io swift codementor help overcome key challenge timely advice speed development process'

### I created initially below model but it was having time complexity of n*n causing lot of computation time

In [26]:
#importing additional lib
# from sklearn.feature_extraction.text import TfidfVectorizer
# from sklearn.metrics.pairwise import linear_kernel
# import time

# Create a DataFrame to store the results
#result_df = pd.DataFrame(columns=['company_name', 'assigned_industry_segment'])

# # calculating cosine similarity for each company description with all industry tags
# tfidf_vectorizer = TfidfVectorizer()

# start time
# start_time = time.time()

# for idx, row in company_data.iterrows():
#     company_name = row['company_name']
#     company_description = row['company_description']

#     preprocessing the company_description by joining the words into a single string
#     company_description = ' '.join(company_description.split())

#     # creating a temporary DataFrame for each company description
#     temp_df = pd.DataFrame(columns=['Industry segment', 'Cosine Similarity'])

#     for idx, industry_row in industry_data.iterrows():
#         industry_segment = industry_row['Industry segment']
#         tags = ' '.join(industry_row['Tags'])  # Concatenate tags with spaces

#         # calculating cosine similarity
#         tfidf_matrix = tfidf_vectorizer.fit_transform([company_description, tags])
#         cosine_sim = linear_kernel(tfidf_matrix[0], tfidf_matrix[1])

#         temp_df = temp_df.append({'Industry segment': industry_segment, 'Cosine Similarity': cosine_sim[0][0]}, ignore_index=True)

#     # finding the industry segment with the highest similarity
#     best_match = temp_df[temp_df['Cosine Similarity'] == temp_df['Cosine Similarity'].max()]
#     assigned_industry_segment = best_match['Industry segment'].values[0]

#     result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_index=True)

#     # calculating elapsed time and estimate remaining time
#     elapsed_time = time.time() - start_time
#     remaining_time = (elapsed_time / (idx + 1)) * (len(company_data) - idx - 1)
#     print(f"Processed {idx + 1}/{len(company_data)} companies. Estimated time remaining: {remaining_time:.2f} seconds")

# # saving the results to a CSV file
# result_df.to_csv('Company_Descriptions_with_Assigned_Tags.csv', index=False)


### Model 2 : more efficient

In [27]:
#Importing additional libraries
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel
import time

In [28]:
# creating a DF to store the results
result_df = pd.DataFrame(columns=['company_name', 'assigned_industry_segment'])

In [29]:
# Ill be calculating cosine similarity for each company description with all industry tags
#based on the similarity scores ill assign industry segment to the company
#initiallizing tf-idf for vectorization, could have used Word2Vec as well
tfidf_vectorizer = TfidfVectorizer()

In [30]:
# preprocessing industry tags and concatenating them with spaces, we can concatenate the tag words with spaces to treat them as a bag of unordered words
industry_data['Tags'] = industry_data['Tags'].apply(lambda tags: ' '.join(tags))

In [31]:
# Fiting and transforming the industry tags
tfidf_matrix = tfidf_vectorizer.fit_transform(industry_data['Tags'])


In [32]:
# initializing start time
start_time = time.time()

for idx, row in company_data.iterrows():
    company_name = row['company_name']
    company_description = ' '.join(row['company_description'].split())

    # calculating cosine similarity
    cosine_sim = linear_kernel(tfidf_vectorizer.transform([company_description]), tfidf_matrix)

    # finding the index of the most similar industry segment
    best_match_index = cosine_sim[0].argmax()
    assigned_industry_segment = industry_data.iloc[best_match_index]['Industry segment']

    result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_index=True)

    # caclulating elapsed time and estimate remaining time
    elapsed_time = time.time() - start_time
    remaining_time = (elapsed_time / (idx + 1)) * (len(company_data) - idx - 1)
    print(f"Processed {idx + 1}/{len(company_data)} companies. Estimated time remaining: {remaining_time:.2f} seconds")


C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_index=True)
C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_index=True)
C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_inde

Processed 1/19965 companies. Estimated time remaining: 37442.07 seconds
Processed 2/19965 companies. Estimated time remaining: 19129.81 seconds
Processed 3/19965 companies. Estimated time remaining: 13020.38 seconds
Processed 4/19965 companies. Estimated time remaining: 9981.93 seconds
Processed 5/19965 companies. Estimated time remaining: 8183.53 seconds


C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_index=True)
C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_index=True)
C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_inde

Processed 6/19965 companies. Estimated time remaining: 6995.61 seconds
Processed 7/19965 companies. Estimated time remaining: 6155.13 seconds
Processed 8/19965 companies. Estimated time remaining: 5484.96 seconds
Processed 9/19965 companies. Estimated time remaining: 4958.34 seconds
Processed 10/19965 companies. Estimated time remaining: 4546.05 seconds


C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_index=True)
C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_index=True)
C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_inde

...

C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_index=True)
C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_index=True)
C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_inde

Processed 19955/19965 companies. Estimated time remaining: 0.41 seconds
Processed 19956/19965 companies. Estimated time remaining: 0.37 seconds
Processed 19957/19965 companies. Estimated time remaining: 0.33 seconds
Processed 19958/19965 companies. Estimated time remaining: 0.29 seconds
Processed 19959/19965 companies. Estimated time remaining: 0.24 seconds
Processed 19960/19965 companies. Estimated time remaining: 0.20 seconds


C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_index=True)
C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_index=True)
C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_inde

Processed 19961/19965 companies. Estimated time remaining: 0.16 seconds
Processed 19962/19965 companies. Estimated time remaining: 0.12 seconds
Processed 19963/19965 companies. Estimated time remaining: 0.08 seconds
Processed 19964/19965 companies. Estimated time remaining: 0.04 seconds
Processed 19965/19965 companies. Estimated time remaining: 0.00 seconds


C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_index=True)
C:\Users\prat9\AppData\Local\Temp\ipykernel_5400\53988011.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result_df = result_df.append({'company_name': company_name, 'assigned_industry_segment': assigned_industry_segment}, ignore_index=True)


In [35]:
# saving the result to a CSV file
result_df.to_csv('Company_with_Assigned_Tags.csv', index=False)


#### BERT can also be used as it is a contextual word embedding model, and can improve classification efficiency. But I needed a GPU to efficiently use BERT for embedding large datasets, therefore simplicity i have followed the above approach